In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.action_chains import ActionChains
from bs4 import BeautifulSoup
import requests
import time
import re
import random

In [2]:
import pandas as pd
import numpy as np

In [3]:
topmovie = pd.read_csv('topmovie.csv')
userlink = topmovie['user-href'].apply(lambda x: x.replace('?ref_=tt_urv','reviews'))
print(userlink[0:10])

0     https://www.imdb.com/user/ur2419668/reviews
1    https://www.imdb.com/user/ur70082814/reviews
2     https://www.imdb.com/user/ur2753508/reviews
3    https://www.imdb.com/user/ur11028498/reviews
4     https://www.imdb.com/user/ur6321000/reviews
5    https://www.imdb.com/user/ur39306660/reviews
6     https://www.imdb.com/user/ur0671675/reviews
7     https://www.imdb.com/user/ur1377045/reviews
8     https://www.imdb.com/user/ur2369479/reviews
9     https://www.imdb.com/user/ur0455602/reviews
Name: user-href, dtype: object


In [10]:
rating = pd.read_csv('rating1.csv')
last_user = rating.iloc[-1,0]
print(last_user)
for i in range(len(userlink)):
    if last_user in userlink[i]:
        last_user_i = i
        print(i)
        print(userlink[i])

ur73645337
1826
https://www.imdb.com/user/ur73645337/reviews


In [5]:
from selenium.webdriver.common.proxy import Proxy
from selenium.webdriver.common.proxy import ProxyType
def get_proxy():
    #5010：settings中设置的监听端口，不是Redis服务的端口
    return requests.get("http://127.0.0.1:5010/get/").json()

def delete_proxy(proxy):
    requests.get("http://127.0.0.1:5010/delete/?proxy={}".format(proxy))

def getNumberReviews(url):
    retry_count = 5
    while(retry_count >0):
        proxy_info = get_proxy().get("proxy")
        print(proxy_info)
        browser_options = webdriver.ChromeOptions()
        browser_options.add_argument('blink-settings=imagesEnabled=false')
        browser_options.add_argument('headless')
        
        proxy = Proxy(
            {
                'proxyType': ProxyType.MANUAL,
                'httpProxy': proxy_info  # 代理ip和端口
            }
        )
        desired_capabilities = webdriver.DesiredCapabilities.CHROME.copy()
        proxy.add_to_capabilities(desired_capabilities)
        browser = webdriver.Chrome(desired_capabilities = desired_capabilities,options=browser_options)
        browser.set_page_load_timeout(10)
        browser.get(url)
        soup_pre = BeautifulSoup(browser.page_source, 'html.parser')

        header = soup_pre.find_all('div',{'class':'header'})[0]
        try: 
            NumberReviews = header.find('div').text
            N = re.search(r'[0-9,.]*',NumberReviews).group()
            N = int(''.join(N.split(',')))
            print(N)
            browser.quit()
            return N, proxy_info
        except AttributeError:
            browser.quit()
            retry_count -= 1

In [9]:
chromedriver_path = '"C:\Program Files\Google\Chrome\Application\chrome.exe"'

for i in range(1000,2000):
    url = userlink[i]
    N, proxy_info = getNumberReviews(url)
    browser_options = webdriver.ChromeOptions()
    browser_options.add_argument('blink-settings=imagesEnabled=false')
    browser_options.add_argument('headless')
    proxy = Proxy(
        {
            'proxyType': ProxyType.MANUAL,
            'httpProxy': proxy_info  # 代理ip和端口
        }
    )
    desired_capabilities = webdriver.DesiredCapabilities.CHROME.copy()
    proxy.add_to_capabilities(desired_capabilities)
    browser = webdriver.Chrome(desired_capabilities = desired_capabilities,options=browser_options)
    browser.set_page_load_timeout(10)
    
    try:
        browser.get(url)
    except:
        break
    print(url)

# 解析 HTML 页面 
    if(19<N<2000):
        while (True):
            try:
                # 找到“加载”按钮元素并点击
                button = browser.find_element(By.ID,'load-more-trigger')
                button.click()
                # 等待一段时间，以让页面加载完成
                time.sleep(2)
            
            except:
                # 如果找不到“加载”按钮，或者出现异常，结束循环
                break
        soup = BeautifulSoup(browser.page_source, 'html.parser')
        reviews = soup.find_all('div', {'class': 'lister-item-content'})
        rows = []
        
    
        for review in reviews:
            try:
                title = review.find('a').text
                print(title,end = '')
            except AttributeError:
                title = ''
            try:
                movie_id = review.find('a')['href'].split('/')[2]
                print(movie_id,end = '')
            except AttributeError:
                movie_id = ''
            try:
                date = review.find('span', {'class': 'review-date'}).text.strip()
                print(date,end = '')
            except AttributeError:
                date = ''
            try:
                score = review.find('span', {'class': 'rating-other-user-rating'}).text.strip()
                score = int(score[0:score.find('/')])
                print(score)
            except AttributeError:
                score = ''
            try:
                des = review.find('div', {'class': 'episode-info text-muted unbold'}).text
                print(des)
            except AttributeError:
                des = ''
            rows.append({'User ID': url.split('/')[-2], 'Movie ID': movie_id, 'Score': score, 'Date': date, 'Title': title,'Tag':des})

    # 将数据转换为 DataFrame
        df = pd.DataFrame(rows)
        df.to_csv('rating1.csv',mode='a',header = False, index = False)
browser.quit()

123.183.160.83:9091
260
https://www.imdb.com/user/ur35307871/reviews
Mindhuntertt529038219 October 2017Get Outtt505244819 May 20178
Alien: Covenanttt231620412 May 20177
Guardians of the Galaxy Vol. 2tt389619826 April 20177
Personal Shoppertt471478214 April 20176
Power Rangerstt37174907 April 20175
Ghost in the Shelltt12198274 April 20175
Lifett544243025 March 20174
Beauty and the Beasttt277120022 March 20177
John Wick: Chapter 2tt442520020 March 20177
Kong: Skull Islandtt373156210 March 20175
Logantt33153423 March 20178
Manchester by the Seatt403422818 February 20178
Moonlighttt497572216 February 20178
The Lego Batman Moviett411628411 February 20177
The Edge of Seventeentt18788701 February 20178
Ellett37165301 February 20178
Splittt497258229 January 20175
Arrivaltt254316420 January 20179
Alliedtt364042416 January 20177
Sherlocktt147558216 January 2017The Foundertt427682015 January 20176
Silencett049021513 January 20175
Don't Think Twicett49720628 January 20178
Forushandett51867145 Janu

IndexError: list index out of range

In [ ]:
#ur2467618

'https://www.imdb.com/user/ur2467618/reviews'

In [ ]:
# 要爬取的IMDb电影页面的链接列表
movie_urls = [
    'https://www.imdb.com/title/tt0111161/',  # The Shawshank Redemption
    'https://www.imdb.com/title/tt0068646/',  # The Godfather
    'https://www.imdb.com/title/tt0071562/',  # The Godfather: Part II
    'https://www.imdb.com/title/tt0468569/',  # The Dark Knight
    'https://www.imdb.com/title/tt0050083/',  # 12 Angry Men
]

# 循环遍历电影链接列表
for url in movie_urls:
    # 发送GET请求获取网页内容
    response = requests.get(url)

    # 如果请求成功，解析HTML页面
    if response.status_code == 200:
        # 使用BeautifulSoup库解析页面
        soup = BeautifulSoup(response.content, 'html.parser')

        # 获取电影标题
        title = soup.find('div', class_='title_wrapper').h1.text.strip()

        # 获取电影评分
        rating = soup.find('span', itemprop='ratingValue').text.strip()

        # 获取电影类型
        genres = [genre.text.strip() for genre in soup.find_all('span', itemprop='genre')]

        # 获取电影时长
        duration = soup.find('time', itemprop='duration')['datetime'].replace('PT', '').replace('M', 'min')

        # 获取电影导演
        director = soup.find('span', itemprop='director').a.text.strip()

        # 获取电影主演
        cast = [actor.text.strip() for actor in soup.find('table', class_='cast_list').find_all('span', itemprop='name')]

        # 打印电影信息
        print('Title:', title)
        print('Rating:', rating)
        print('Genres:', genres)
        print('Duration:', duration)
        print('Director:', director)
        print('Cast:', cast)
        print('--------------------------------------------------')
    else:
        print('Failed to retrieve the webpage at', url)